In [1]:
import numpy as np
import bilby 
import pycbc 
import sys
import matplotlib.pyplot as plt

import zuko
import torch
from torch.utils.data import Dataset, DataLoader
from torch import nn

import pickle
from sklearn.decomposition import IncrementalPCA
import sklearn.decomposition 

/home/qian.hu/.conda/envs/myigwn-py39/lib/python3.9/site-packages/pycbc/types/array.py:36: UserWarning: Wswiglal-redir-stdio:

SWIGLAL standard output/error redirection is enabled in IPython.
This may lead to performance penalties. To disable locally, use:

with lal.no_swig_redirect_standard_output_error():
    ...

To disable globally, use:

lal.swig_redirect_standard_output_error(True)

Note however that this will likely lead to error messages from
LAL functions being either misdirected or lost when called from
Jupyter notebooks.

To suppress this warning, use:

import warnings
warnings.filterwarnings("ignore", "Wswiglal-redir-stdio")
import lal

  import lal as _lal


In [10]:
import river.data
from river.data.datagenerator import DataGeneratorBilbyFD
from river.data.dataset import DatasetStrainFD, DatasetStrainFDFromPreCalSVDWF
#import river.data.utils as datautils
from river.data.utils import *

from river.models import embedding
from river.models.utils import *

In [7]:
import json

# train3.py

In [11]:
config_path = '/home/qian.hu/mlpe/river/scripts/trained_models/GlasNSFConv1DRes_100ktest'
with open(f"{config_path}/config.json", 'r') as f:
    config = json.load(f)

config_datagenerator = config['data_generator_parameters']
config_training = config['training_parameters']
config_model = config['model_parameters']
config_precalwf = config['precalwf_parameters']


detector_names = config_datagenerator['detector_names']

#Nsample = config_training['Nsample']
#Nvalid = config_training['Nvalid']
Nsample = config_precalwf['train']['nbatch'] * config_precalwf['train']['file_per_batch'] * config_precalwf['train']['sample_per_file'] 
Nvalid = config_precalwf['valid']['nbatch'] * config_precalwf['valid']['file_per_batch'] * config_precalwf['valid']['sample_per_file'] 
Ntest = config_training['Ntest']

#selection_factor = 2
selection_factor = config_datagenerator['selection_factor'] # make sure there are enough SNR>8 samples in injection_parameters
injection_parameters_test = generate_BNS_injection_parameters(Nsample = Ntest*selection_factor, **config_datagenerator)

data_generator_train = DataGeneratorBilbyFD(**config_datagenerator)
data_generator_valid = DataGeneratorBilbyFD(**config_datagenerator)
config_datagenerator_test = config_datagenerator.copy()
config_datagenerator_test['ipca'] = None 
data_generator_test = DataGeneratorBilbyFD(**config_datagenerator_test)

data_generator_test.inject_signals(injection_parameters_test, Ninj=Ntest*selection_factor, Nneeded =Ntest)
data_generator_test.numpy_starins()

ipca_path = config['model_parameters']['ipca_path']
ipca_gen = load_model(ipca_path)


train_precalwf_list = get_precalwf_list(**config_precalwf['train'])
valid_precalwf_list = get_precalwf_list(**config_precalwf['valid'])

dataset_train = DatasetStrainFDFromPreCalSVDWF(train_precalwf_list, config_datagenerator['context_parameter_names'], data_generator_train,ipca_gen=ipca_gen,
                                                dmin=config_datagenerator['d_min'], dmax=config_datagenerator['d_max'], dpower=config_datagenerator['d_power'])
dataset_valid = DatasetStrainFDFromPreCalSVDWF(valid_precalwf_list, config_datagenerator['context_parameter_names'], data_generator_valid,ipca_gen=ipca_gen,
                                                dmin=config_datagenerator['d_min'], dmax=config_datagenerator['d_max'], dpower=config_datagenerator['d_power'])
dataset_test = DatasetStrainFD(data_dict=data_generator_test.data, parameter_names=config_datagenerator['context_parameter_names'])

12:22 bilby INFO    : Waveform generator initiated with
  frequency_domain_source_model: bilby.gw.source.lal_binary_neutron_star
  time_domain_source_model: None
  parameter_conversion: bilby.gw.conversion.convert_to_lal_binary_black_hole_parameters


Using bilby_default PSDs to generate data.


12:22 bilby INFO    : Waveform generator initiated with
  frequency_domain_source_model: bilby.gw.source.lal_binary_neutron_star
  time_domain_source_model: None
  parameter_conversion: bilby.gw.conversion.convert_to_lal_binary_black_hole_parameters


Using bilby_default PSDs to generate data.


12:22 bilby INFO    : Waveform generator initiated with
  frequency_domain_source_model: bilby.gw.source.lal_binary_neutron_star
  time_domain_source_model: None
  parameter_conversion: bilby.gw.conversion.convert_to_lal_binary_black_hole_parameters


Using bilby_default PSDs to generate data.
Injecting 0-th signal, 0.0% done
Injecting 1-th signal, 5.0% done
Injecting 2-th signal, 10.0% done
Injecting 3-th signal, 15.0% done
Injecting 4-th signal, 20.0% done
Injecting 5-th signal, 25.0% done
Injecting 6-th signal, 30.0% done
Injecting 7-th signal, 35.0% done
Injecting 8-th signal, 40.0% done
Injecting 9-th signal, 45.0% done
Model loaded from /home/qian.hu/mlpe/river/scripts/ipca_models/lhv/IPCA_BNSFD_10000to256_ExpUnwrap_fixtc_lowspin_200Mpc.pickle


In [23]:
#batch_size_train = config_training['batch_size_train']
#batch_size_valid = config_training['batch_size_valid']
batch_size_test = config_training['batch_size_test']

batch_size_train = 10
batch_size_valid = 10
train_loader = DataLoader(dataset_train, batch_size=batch_size_train, shuffle=True)
valid_loader = DataLoader(dataset_valid, batch_size=batch_size_valid, shuffle=True)
test_loader = DataLoader(dataset_test, batch_size=batch_size_test, shuffle=False)


In [32]:
theta, x = dataset_train[0]

In [35]:
xx = x.squeeze(0)

In [36]:
xx.shape

torch.Size([9, 256])

In [38]:
xxx = xx.numpy()

In [28]:
for theta, x in train_loader:
    break

In [30]:
x.shape

torch.Size([10, 1, 9, 256])

In [31]:
theta.shape

torch.Size([10, 17])

In [40]:
data_dict = data_generator_test.data
s = np.array(list(data_dict['strains'][detname] for detname in detector_names ))

In [42]:
s.shape

(3, 10, 321281)

In [45]:
strain = torch.from_numpy(s*1e23).movedim(0,1)

In [46]:
strain.shape

torch.Size([10, 3, 321281])

In [64]:
%time dd = load_dict_from_hdf5('/home/qian.hu/mlpe/training_data/bns_320s_dataproj_lowspin/valid/batch0/bns_320s_dataproj_lowspin_0.h5')

CPU times: user 16.6 ms, sys: 14.2 ms, total: 30.8 ms
Wall time: 60.7 ms


In [58]:
dd['x'][0].shape

(9, 256)

In [61]:
%time data_generator_test.inject_signals(injection_parameters_test, Ninj=Ntest*selection_factor, Nneeded =Ntest)

Injecting 0-th signal, 0.0% done
Injecting 1-th signal, 5.0% done
Injecting 2-th signal, 10.0% done
Injecting 3-th signal, 15.0% done
Injecting 4-th signal, 20.0% done
Injecting 5-th signal, 25.0% done
Injecting 6-th signal, 30.0% done
Injecting 7-th signal, 35.0% done
Injecting 8-th signal, 40.0% done
Injecting 9-th signal, 45.0% done
CPU times: user 8.39 s, sys: 159 ms, total: 8.55 s
Wall time: 8.93 s


In [60]:
data_generator_test.initialize_data()

# make PCA

In [3]:
Nsample_template = 10000
injection_parameters_template = generate_BNS_injection_parameters(
        Nsample_template,
        a_max=0.1,
        d_min=10,
        d_max=100,
        d_power=2,
        tc_min=-0.1
        tc_max=0.1)

In [4]:
source_type = 'BNS'
detector_names = ['H1', 'L1', 'V1'] 
duration = 32
f_low = 20
f_ref = 20
sampling_frequency = 2048
waveform_approximant = 'IMRPhenomPv2_NRTidal'
parameter_names = PARAMETER_NAMES_PRECESSINGBNS_BILBY
PSD_type = 'bilby_default' #'zero_noise'
use_sealgw_detector = True

In [5]:
data_template_generator = DataGeneratorBilbyFD(source_type,
            detector_names, 
            duration, 
            f_low, 
            f_ref, 
            sampling_frequency, 
            waveform_approximant, 
            parameter_names,
            PSD_type='zero_noise',
            use_sealgw_detector=use_sealgw_detector)

11:57 bilby INFO    : Waveform generator initiated with
  frequency_domain_source_model: bilby.gw.source.lal_binary_neutron_star
  time_domain_source_model: None
  parameter_conversion: bilby.gw.conversion.convert_to_lal_binary_black_hole_parameters


Using zero_noise PSDs to generate data.


In [7]:
data_template_generator.inject_signals(injection_parameters_template, Nsample_template)

11:58 bilby WARNING : The injected signal has a duration in-band of 60.3s, but the data for detector H1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 60.3s, but the data for detector L1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 60.3s, but the data for detector V1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 105.0s, but the data for detector H1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 105.0s, but the data for detector L1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 105.0s, but the data for detector V1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 87.7s, but the data for detector H1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 87.7s, but the data for detector L1 has a durat

Injecting 0-th signal, 0.0% done
Injecting 1-th signal, 0.01% done
Injecting 2-th signal, 0.02% done
Injecting 3-th signal, 0.03% done
Injecting 4-th signal, 0.04% done


11:58 bilby WARNING : The injected signal has a duration in-band of 91.1s, but the data for detector H1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 91.1s, but the data for detector L1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 91.1s, but the data for detector V1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 66.6s, but the data for detector H1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 66.6s, but the data for detector L1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 66.6s, but the data for detector V1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 170.8s, but the data for detector H1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 170.8s, but the data for detector L1 has a durati

Injecting 5-th signal, 0.05% done
Injecting 6-th signal, 0.06% done
Injecting 7-th signal, 0.07% done
Injecting 8-th signal, 0.08% done
Injecting 9-th signal, 0.09% done
Injecting 10-th signal, 0.1% done


11:58 bilby WARNING : The injected signal has a duration in-band of 83.5s, but the data for detector H1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 83.5s, but the data for detector L1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 83.5s, but the data for detector V1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 180.7s, but the data for detector H1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 180.7s, but the data for detector L1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 180.7s, but the data for detector V1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 90.7s, but the data for detector H1 has a duration of 32s
11:58 bilby WARNING : The injected signal has a duration in-band of 90.7s, but the data for detector L1 has a durat

...

Injecting 9986-th signal, 99.86% done
Injecting 9987-th signal, 99.87% done
Injecting 9988-th signal, 99.88% done
Injecting 9989-th signal, 99.89% done
Injecting 9990-th signal, 99.9% done


12:05 bilby WARNING : The injected signal has a duration in-band of 78.8s, but the data for detector H1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 78.8s, but the data for detector L1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 78.8s, but the data for detector V1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 95.6s, but the data for detector H1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 95.6s, but the data for detector L1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 95.6s, but the data for detector V1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 138.1s, but the data for detector H1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 138.1s, but the data for detector L1 has a durati

Injecting 9991-th signal, 99.91% done
Injecting 9992-th signal, 99.92% done
Injecting 9993-th signal, 99.93% done
Injecting 9994-th signal, 99.94% done
Injecting 9995-th signal, 99.95% done


12:05 bilby WARNING : The injected signal has a duration in-band of 140.2s, but the data for detector H1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 140.2s, but the data for detector L1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 140.2s, but the data for detector V1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 94.1s, but the data for detector H1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 94.1s, but the data for detector L1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 94.1s, but the data for detector V1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 64.6s, but the data for detector H1 has a duration of 32s
12:05 bilby WARNING : The injected signal has a duration in-band of 64.6s, but the data for detector L1 has a durat

Injecting 9996-th signal, 99.96% done
Injecting 9997-th signal, 99.97% done
Injecting 9998-th signal, 99.98% done
Injecting 9999-th signal, 99.99% done


In [8]:
data_template_generator.numpy_starins()
data_template_generator.scale_strains()

In [9]:
n_components=500
ipca_gen = embedding.pca.IPCAGenerator(data_template_generator.data['strains'], n_components, detector_names, decomposition='exp_unwrap')

Generating PCA for H1
Generating PCA for L1
Generating PCA for V1


In [10]:
modelutils.save_model('IPCA_BNSFD_10000to500_ExpUnwrap.pickle', ipca_gen)

Model saved to IPCA_BNSFD_10000to500_ExpUnwrap.pickle


# training

In [39]:
source_type = 'BNS'
detector_names = ['H1', 'L1', 'V1'] 
duration = 32
f_low = 20
f_ref = 20
sampling_frequency = 2048
waveform_approximant = 'IMRPhenomPv2_NRTidal'
parameter_names = PARAMETER_NAMES_PRECESSINGBNS_BILBY
PSD_type = 'bilby_default' #'zero_noise'
use_sealgw_detector = True

In [40]:
ipca_gen = modelutils.load_model('/data/wiay/qian/river/scripts/ipca_models/IPCA_BNSFD_10000to500_ExpUnwrap.pickle')

Nsample = 1000
Ntest = 100
injection_parameters_valid = generate_BNS_injection_parameters(Ntest,
        a_max=0.1,
        d_min=10,
        d_max=100,
        d_power=2)

injection_parameters_train = generate_BNS_injection_parameters(Nsample,
        a_max=0.1,
        d_min=10,
        d_max=100,
        d_power=2)

data_generator_train = DataGeneratorBilbyFD(source_type,
            detector_names, 
            duration, 
            f_low, 
            f_ref, 
            sampling_frequency, 
            waveform_approximant, 
            parameter_names,
            PSD_type=PSD_type,
            use_sealgw_detector=use_sealgw_detector)

data_generator_valid = DataGeneratorBilbyFD(source_type,
            detector_names, 
            duration, 
            f_low, 
            f_ref, 
            sampling_frequency, 
            waveform_approximant, 
            parameter_names,
            PSD_type=PSD_type,
            use_sealgw_detector=use_sealgw_detector)



17:16 bilby INFO    : Waveform generator initiated with
  frequency_domain_source_model: bilby.gw.source.lal_binary_neutron_star
  time_domain_source_model: None
  parameter_conversion: bilby.gw.conversion.convert_to_lal_binary_black_hole_parameters
17:16 bilby INFO    : Waveform generator initiated with
  frequency_domain_source_model: bilby.gw.source.lal_binary_neutron_star
  time_domain_source_model: None
  parameter_conversion: bilby.gw.conversion.convert_to_lal_binary_black_hole_parameters


Model loaded from /data/wiay/qian/river/scripts/ipca_models/IPCA_BNSFD_10000to500_ExpUnwrap.pickle
Using bilby_default PSDs to generate data.
Using bilby_default PSDs to generate data.


In [41]:
data_generator_train.inject_signals(injection_parameters_train, Nsample)
data_generator_train.numpy_starins()

data_generator_valid.inject_signals(injection_parameters_valid, Ntest)
data_generator_valid.numpy_starins()


17:16 bilby WARNING : The injected signal has a duration in-band of 167.1s, but the data for detector H1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 167.1s, but the data for detector L1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 167.1s, but the data for detector V1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 131.2s, but the data for detector H1 has a duration of 32s


Injecting 0-th signal, 0.0% done
Injecting 1-th signal, 0.1% done


17:16 bilby WARNING : The injected signal has a duration in-band of 131.2s, but the data for detector L1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 131.2s, but the data for detector V1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 159.9s, but the data for detector H1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 159.9s, but the data for detector L1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 159.9s, but the data for detector V1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 59.9s, but the data for detector H1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 59.9s, but the data for detector L1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 59.9s, but the data for detector V1 has a dur

Injecting 2-th signal, 0.2% done
Injecting 3-th signal, 0.3% done
Injecting 4-th signal, 0.4% done
Injecting 5-th signal, 0.5% done


17:16 bilby WARNING : The injected signal has a duration in-band of 103.3s, but the data for detector L1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 103.3s, but the data for detector V1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 110.9s, but the data for detector H1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 110.9s, but the data for detector L1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 110.9s, but the data for detector V1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 166.6s, but the data for detector H1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 166.6s, but the data for detector L1 has a duration of 32s
17:16 bilby WARNING : The injected signal has a duration in-band of 166.6s, but the data for detector V1 has a 

...

Injecting 88-th signal, 88.0% done
Injecting 89-th signal, 89.0% done
Injecting 90-th signal, 90.0% done
Injecting 91-th signal, 91.0% done
Injecting 92-th signal, 92.0% done


17:17 bilby WARNING : The injected signal has a duration in-band of 54.8s, but the data for detector H1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 54.8s, but the data for detector L1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 54.8s, but the data for detector V1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 115.4s, but the data for detector H1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 115.4s, but the data for detector L1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 115.4s, but the data for detector V1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 121.7s, but the data for detector H1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 121.7s, but the data for detector L1 has a dur

Injecting 93-th signal, 93.0% done
Injecting 94-th signal, 94.0% done
Injecting 95-th signal, 95.0% done
Injecting 96-th signal, 96.0% done


17:17 bilby WARNING : The injected signal has a duration in-band of 121.9s, but the data for detector H1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 121.9s, but the data for detector L1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 121.9s, but the data for detector V1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 67.1s, but the data for detector H1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 67.1s, but the data for detector L1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 67.1s, but the data for detector V1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 98.2s, but the data for detector H1 has a duration of 32s
17:17 bilby WARNING : The injected signal has a duration in-band of 98.2s, but the data for detector L1 has a durat

Injecting 97-th signal, 97.0% done
Injecting 98-th signal, 98.0% done
Injecting 99-th signal, 99.0% done


In [42]:
dataset_train = DatasetStrainFD(data_dict=data_generator_train.data, parameter_names=PARAMETER_NAMES_PRECESSINGBNS_BILBY)
dataset_valid = DatasetStrainFD(data_dict=data_generator_valid.data, parameter_names=PARAMETER_NAMES_PRECESSINGBNS_BILBY)

In [43]:
batch_size = 64
train_loader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True)
valid_loader = DataLoader(dataset_valid, batch_size=batch_size, shuffle=False)

In [44]:
def train_zukoflow(flow, embedding, optimizer, dataloader, detector_names, ipca_gen, device='cpu'):
    flow.train()
    loss_list = []
    for theta, strain, psd in dataloader:
        inputs = project_strain_data_FDAPhi(strain, psd, detector_names, ipca_gen).to(device)
        theta = theta.to(device)
        embedding_out = embedding(inputs)
        optimizer.zero_grad()

        loss = -flow(embedding_out).log_prob(theta).mean() # mean(list of losses of elements in this batch)
        loss_list.append(loss.detach())
        loss.backward()
        optimizer.step()

    mean_loss = torch.stack(loss_list).mean().item() # mean(list of mean losses of each batch)
    std_loss = torch.stack(loss_list).std().item()
    return mean_loss, std_loss

def eval_zukoflow(flow, embedding, dataloader, detector_names, ipca_gen, device='cpu'):
    flow.eval()
    loss_list = []
    with torch.no_grad():
        for theta, strain, psd in dataloader:
            inputs = project_strain_data_FDAPhi(strain, psd, detector_names, ipca_gen).to(device)
            theta = theta.to(device)
            embedding_out = embedding(inputs)

            loss = -flow(embedding_out).log_prob(theta).mean()
            loss_list.append(loss.detach())

    mean_loss = torch.stack(loss_list).mean().item()
    std_loss = torch.stack(loss_list).std().item()
    return mean_loss, std_loss

        

    


In [45]:
n_components = ipca_gen.n_components
device='cuda'

Net_embedding = EmbeddingConv(ndet=3, ncomp=n_components, nout=128, middle_channel=1024).to(device)
#optimizer_embd = optim.Adam(Net_embedding.parameters(), lr=1e-3)
#scheduler_embd = StepLR(optimizer_embd, step_size=1, gamma=0.7)

flow = zuko.flows.NSF(features=17, context=128, transforms=100, hidden_features=(640, 640)).to(device)
#optimizer_flow = optim.Adam(flow.parameters(), lr=1e-4)
#scheduler_flow = StepLR(optimizer_flow, step_size=1, gamma=0.7)

optimizer = torch.optim.Adam(list(Net_embedding.parameters()) + list(flow.parameters()), lr=1e-3)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=100, gamma=0.7)



In [27]:
theta, strain, psd = dataset_train[0:2]
test_input = project_strain_data_FDAPhi(strain, psd, detector_names, ipca_gen).float().to('cpu')
embedding_out = Net_embedding(test_input).float().to('cpu')
-flow(embedding_out.to('cpu')).log_prob(theta.to('cpu'))

tensor([3.8871e+14, 3.7987e+14], grad_fn=<NegBackward0>)

In [46]:
max_epoch = 200000

epoches_update = 10000

train_losses = []
valid_losses = []
for epoch in range(max_epoch):
    #losses = []
    
    if epoch % epoches_update == 0 and epoch!=0:
        data_generator_train.initialize_data()
        injection_parameters_train = generate_BNS_injection_parameters(Nsample, a_max=0.1, d_min=10, d_max=100, d_power=2)
        data_generator_train.inject_signals(injection_parameters_train, Nsample)
        data_generator_train.numpy_starins()
        dataset_train = DatasetStrainFD(data_dict=data_generator_train.data, parameter_names=PARAMETER_NAMES_PRECESSINGBNS_BILBY)
        train_loader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True)
        print(f"Training data updated at epoch={epoch}")

    train_loss, train_loss_std = train_zukoflow(flow, Net_embedding, optimizer, train_loader, detector_names, ipca_gen, device=device)
    valid_loss, valid_loss_std = eval_zukoflow(flow, Net_embedding, valid_loader, detector_names, ipca_gen, device=device)

    train_losses.append(train_loss)
    valid_losses.append(valid_loss)

    print(f'epoch {epoch}, train loss = {train_loss}±{train_loss_std}, valid loss = {valid_loss}±{valid_loss_std}')

    if valid_loss<min(valid_losses):
        best_epoch = epoch
        torch.save(Net_embedding.state_dict(), 'ckpt_embedding.pickle')
        torch.save(flow.state_dict(), 'ckpt_flow.pickle')
        print(f'Current best epoch: {best_epoch}')

    scheduler.step()

epoch 0, train loss = 165068478087168.0±18182727270400.0, valid loss = 174504051474432.0±7625563963392.0
epoch 1, train loss = 164882552979456.0±19667586383872.0, valid loss = 174504051474432.0±7625563963392.0
epoch 2, train loss = 165191102758912.0±10924961300480.0, valid loss = 174504051474432.0±7625563963392.0
epoch 3, train loss = 164264815886336.0±20142108966912.0, valid loss = 174504051474432.0±7625563963392.0
epoch 4, train loss = 165192612708352.0±21078726410240.0, valid loss = 174504051474432.0±7625563963392.0
epoch 5, train loss = 164793818284032.0±17928743288832.0, valid loss = 174504051474432.0±7625563963392.0
epoch 6, train loss = 165105622843392.0±14002443780096.0, valid loss = 174504051474432.0±7625563963392.0
epoch 7, train loss = 164859350089728.0±21203750223872.0, valid loss = 174504051474432.0±7625563963392.0
epoch 8, train loss = 165944416534528.0±17298146459648.0, valid loss = 174504051474432.0±7625563963392.0
epoch 9, train loss = 165052808167424.0±11285374697472.

KeyboardInterrupt: 